In [1]:
%pip install dbfread

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.3.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
from dbfread import DBF
import psycopg2
import csv
from io import StringIO
from datetime import datetime
from dbfread import DBF

In [5]:
import psycopg2
import psycopg2.extras

# Connect to the PostgreSQL database
conn = psycopg2.connect(
    dbname="bytsscom_unmsm",
    user="postgres",
    password="postgres",
    host="localhost",
    port="5432"
)
conn.autocommit = True
cur = conn.cursor(cursor_factory=psycopg2.extras.DictCursor)

In [6]:
from decimal import Decimal

In [7]:
def certificado():
    cur.execute(
    """
   SELECT c.ano_eje,
       cf.sys_id_certificacion as id_certificacion,
       c.certificado as num_certificado,
       cert.id_area,
       cf.secuencia,
       f.siaf_codigo                        AS sys_id_fuente,
       f.abre_fuente as fuente,
       cla.id_clasificador                AS sys_ID_GENERICA,
       substring(cm.sys_cod_clasif, 1, 2) as GENERICA,
              cm.sys_id_clasificador             AS sys_ID_CLASIFICADOR,
       cm.sys_cod_clasif                  as CLASIFICADOR,
       cs.cod_doc,
       cs.num_doc,
       cf.glosa,
       CASE cf.secuencia_padre
           WHEN '0000' THEN 'DP'
           WHEN '0001' THEN 'CA'
           ELSE '' END                    AS sys_TIPO_CERT,
       sum(cs.monto_nacional)             AS MONTO_NACIONAL,
       sum(cm.monto_nacional)             AS MONTO_CLASIFICADOR,
       cs.estado_envio,
       cs.estado_registro,
       cs.fecha_creacion_clt,
       mt.id_meta_institucional as meta,
        mt.sec_func,
       mp.nomb_met_ins

FROM bytsscom_bytsiaf.certificado c
         INNER JOIN bytsscom_bytsiaf.certificado_fase cf
                    ON c.certificado = cf.certificado
         INNER JOIN bytsscom_bytcore.fuente f
                    ON cf.fuente_financ = f.siaf_codigo
                        AND cf.ano_eje = '2025'
         INNER JOIN bytsscom_bytsiaf.certificado_secuencia cs
                    ON c.certificado = cs.certificado
                        AND cf.secuencia = cs.secuencia
                        AND cs.estado_registro = 'A'
                        AND cs.ano_eje = '2025'
         INNER JOIN bytsscom_bytsiaf.certificado_meta cm
                    ON cf.certificado = cm.certificado
                        AND cf.secuencia = cm.secuencia
                        AND cm.ano_eje = '2025'
         LEFT JOIN bytsscom_bytcore.meta_institucional_siaf mt
                    ON cm.sec_func = mt.sec_func
                    AND mt.id_anio = '2025'::int
         INNER JOIN bytsscom_bytcore.meta_institucional mp
                    ON mt.id_meta_institucional = mp.id_meta_institucional
         INNER JOIN bytsscom_bytcore.clasificador cla
                    ON substring(cm.sys_cod_clasif, 1, 2) = cla.cod_clasif
         LEFT JOIN (SELECT distinct c.id_certificacion,
                                    m.id_area
                    FROM bytsscom_bytsig.vw_certificacion c
                             inner join bytsscom_bytsig.memo_requerimiento m
                                        on c.id_memo_requerimiento = m.id_memo_requerimiento
                    where c.id_anio = 2025
                      AND c.esta_cert = 'A') cert
                   ON cf.sys_id_certificacion = cert.id_certificacion
        INNER join sistema_informacion_gerencial.hechos_institucional_consolidados hic
            on hic.num_certificado = c.certificado
WHERE c.ano_eje = '2025' and cf.secuencia_padre = '0000'
--AND cf.certificado = '0000006928'
GROUP BY c.ano_eje,
         cert.id_area,
         cf.sys_id_certificacion,
         cs.fecha_creacion_clt,
         --cs.fecha_bd_oracle,
         c.certificado,
         cf.secuencia,
         f.id_fuente,
         f.abre_fuente,
        mt.id_meta_institucional,
        mt.sec_func,
        mp.nomb_met_ins,
         cla.id_clasificador,
         cm.sys_id_clasificador,
         cm.sys_cod_clasif,
         cf.secuencia_padre,
         cs.cod_doc,
         cs.num_doc,
         cf.glosa,
         cs.estado_envio,
         cs.estado_registro
ORDER BY c.certificado,
         cf.secuencia,
         cm.sys_cod_clasif;
    """,)
    return cur.fetchall()
  

In [8]:
resultados = certificado()
print(resultados)
for fila in resultados:
    print(fila)

[['2025', 444186, '0000000001', None, '0001', '00', '00-RO', 856, '21', 1894, '21 113 1 1', '086', '00005-2024-OGRRHH   ', 'PLANILLA CAS RO', 'DP', Decimal('8165489.00'), Decimal('966793.00'), 'T', 'A', datetime.date(2025, 1, 8), 17, '0034', 'EJERCICIO DE LA DOCENCIA UNIVERSITARIA /  / '], ['2025', 444186, '0000000001', None, '0001', '00', '00-RO', 856, '21', 1894, '21 113 1 1', '086', '00005-2024-OGRRHH   ', 'PLANILLA CAS RO', 'DP', Decimal('8165489.00'), Decimal('3666579.00'), 'T', 'A', datetime.date(2025, 1, 8), 31, '0050', 'ADMINISTRACION DE LOS RECURSOS HUMANOS, FINANCIEROS Y LOGISTICOS /  / '], ['2025', 444186, '0000000001', None, '0001', '00', '00-RO', 856, '21', 1894, '21 113 1 1', '086', '00005-2024-OGRRHH   ', 'PLANILLA CAS RO', 'DP', Decimal('8165489.00'), Decimal('1507200.00'), 'T', 'A', datetime.date(2025, 1, 8), 139, '0051', ' /  / '], ['2025', 444186, '0000000001', None, '0001', '00', '00-RO', 856, '21', 1895, '21 113 1 2', '086', '00005-2024-OGRRHH   ', 'PLANILLA CAS RO

In [27]:
import pandas as pd
from psycopg2 import errors  #
pd.set_option('display.float_format', '{:,.2f}'.format)

def get_expediente_fase_df():
    raw = resultados
    df = pd.DataFrame(
        raw,
        columns=['ano_eje', 'id_certificacion','num_certificado', 'id_area','secuencia','sys_id_fuente','fuente','sys_id_generica','generica',  
                 'sys_id_clasificador', 'clasificador', 'cod_doc','num_doc','glosa','sys_tipo_cert','monto_nacional','monto_clasificador',
                 'estado_envio', 'estado_registro', 'fecha_creacion_clt','meta','sec_func','nomb_met_ins'
                 ]
    )
    df['monto_nacional'] = df['monto_nacional'].astype(float)
    df['monto_clasificador'] = df['monto_clasificador'].astype(float)
    
    df.replace({"NaN": pd.NA, "": pd.NA}, inplace=True)
    df.fillna(0, inplace=True)
    df['id_area'] = df['id_area'].astype(int)
    
    return df

# Uso
df_1 = get_expediente_fase_df()
df_1['glosa'] = df_1['glosa'].str.replace(r"[\"']", "", regex=True)
print(df_1)

     ano_eje  id_certificacion num_certificado  id_area secuencia  \
0       2025        444,186.00      0000000001        0      0001   
1       2025        444,186.00      0000000001        0      0001   
2       2025        444,186.00      0000000001        0      0001   
3       2025        444,186.00      0000000001        0      0001   
4       2025        444,186.00      0000000001        0      0001   
...      ...               ...             ...      ...       ...   
3136    2025        450,339.00      0000002533    10469      0001   
3137    2025        450,349.00      0000002536    11420      0001   
3138    2025        450,363.00      0000002542    11420      0001   
3139    2025        450,365.00      0000002544    10350      0001   
3140    2025        450,367.00      0000002545    10879      0001   

     sys_id_fuente  fuente  sys_id_generica generica  sys_id_clasificador  \
0               00   00-RO              856       21                 1894   
1               0

In [ ]:
import pandas as pd

def create_insert_consolidado(row):

    def val(v):
        # Si quisieras tratar None o NaN:
        if pd.isna(v):
            return 'NULL'
        return v

    query = f"""
    INSERT INTO sistema_informacion_gerencial.dm_certificado
      (ano_eje, id_certificacion, num_certificado, id_area, secuencia, sys_id_fuente, fuente, sys_id_generica, generica, sys_id_clasificador, clasificador, cod_doc, num_doc, glosa, sys_tipo_cert, monto_nacional, monto_clasificador, estado_envio, estado_registro, fecha_creacion_clt, meta, sec_func, nomb_met_ins)
    VALUES (
       {int(val(row['ano_eje']))}::integer,
      '{val(row['id_certificacion'])}'::integer,
      '{val(row['num_certificado'])}'::varchar,
       {int(val(row['id_area']))}::integer,
      '{val(row['secuencia'])}'::varchar,
       {int(val(row['sys_id_fuente']))}::integer,
        '{val(row['fuente'])}'::varchar,
        {int(val(row['sys_id_generica']))}::integer,
        '{val(row['generica'])}'::varchar,
        {int(val(row['sys_id_clasificador']))}::integer,
        '{val(row['clasificador'])}'::varchar,
        '{val(row['cod_doc'])}'::varchar,
        '{val(row['num_doc'])}'::varchar,
        '{val(row['glosa'])}'::varchar,
        '{val(row['sys_tipo_cert'])}'::varchar,
        {float(val(row['monto_nacional']))}::numeric,
        {float(val(row['monto_clasificador']))}::numeric,
        '{val(row['estado_envio'])}'::varchar,
        '{val(row['estado_registro'])}'::varchar,
        '{val(row['fecha_creacion_clt'])}'::timestamp,
        '{val(row['meta'])}'::varchar,
        '{val(row['sec_func'])}'::varchar,
        '{val(row['nomb_met_ins'])}'::varchar
      
    )
    ON CONFLICT DO NOTHING;
    """
    # Lo comprimimos en una sola línea si lo quieres así
    return query.replace("\n", " ")

# --- Uso ---

# Generas todos los INSERTs
insert_statements = [
    create_insert_consolidado(row)
    for _, row in df_1.iterrows()
]

# Opcional: los imprimes o los ejecutas
for sql in insert_statements:
    print(sql)
    # cur.execute(sql)  # si quieres ejecutarlos directamente
# conn.commit()

     INSERT INTO sistema_informacion_gerencial.dm_certificado       (ano_eje, id_certificacion, num_certificado, id_area, secuencia, sys_id_fuente, fuente, sys_id_generica, generica, sys_id_clasificador, clasificador, cod_doc, num_doc, glosa, sys_tipo_cert, monto_nacional, monto_clasificador, estado_envio, estado_registro, fecha_creacion_clt, meta, sec_func, nomb_met_ins)     VALUES (        2025::integer,       '444186.0'::varchar,       '0000000001'::varchar,        0::integer,       '0001'::varchar,        0::integer,         '00-RO'::varchar,         856::integer,         '21'::varchar,         1894::integer,         '21 113 1 1'::varchar,         '086'::varchar,         '00005-2024-OGRRHH   '::varchar,         'PLANILLA CAS RO'::varchar,         'DP'::varchar,         8165489.0::numeric,         966793.0::numeric,         'T'::varchar,         'A'::varchar,         '2025-01-08'::timestamp,         '17'::varchar,         '0034'::varchar,         'EJERCICIO DE LA DOCENCIA UNIVERSITA

In [29]:
output_path = 'insert_dm_certificado.sql'

with open(output_path, 'w', encoding='utf-8') as f:
    # Escribimos cada sentencia en una línea nueva
    for sql in insert_statements:
        f.write(sql + '\n')

print(f"Archivo SQL generado en: {output_path}")

Archivo SQL generado en: insert_dm_certificado.sql
